In [ ]:
!pip install transformers datasets evaluate bert-score shap

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 15.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 20.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 119.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 91.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 61.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
# Install BARTScore from GitHub
!git clone https://github.com/neulab/BARTScore.git



Cloning into 'BARTScore'...
remote: Enumerating objects: 220, done.
remote: Counting objects: 100% (26/26), done.
remote: Compressing objects: 100% (12/12), done.
remote: Total 220 (delta 18), reused 14 (delta 14), pack-reused 194 (from 1)
Receiving objects: 100% (220/220), 101.98 MiB | 21.50 MiB/s, done.
Resolving deltas: 100% (47/47), done.
Updating files: 100% (192/192), done.


In [ ]:
%cd BARTScore


/content/BARTScore


In [ ]:
!pip install transformers rouge-score nltk


  Preparing metadata (setup.py) ... done
  Created wheel for rouge-score: filename=rouge_score-0.1.2-py3-none-any.whl size=24934 sha256=3a7b333271a0490585632f10a4c18cfaedf9634b95f5901812cce3835f50fa8d
  Stored in directory: /root/.cache/pip/wheels/1e/19/43/8a442dc83660ca25e163e1bd1f89919284ab0d0c1475475148
Successfully built rouge-score


In [ ]:
# from transformers import BartTokenizer, BartForConditionalGeneration
# import torch

# tokenizer = BartTokenizer.from_pretrained('')
# model = BartForConditionalGeneration.from_pretrained('')
# model.eval()

# def compute_bart_score(candidate, reference):
#     inputs = tokenizer(candidate, return_tensors='pt')
#     with torch.no_grad():
#         outputs = model(**inputs, labels=tokenizer(reference, return_tensors='pt')['input_ids'])
#         loss = outputs.loss
#     return -loss.item()

# score = compute_bart_score("This is the generated answer.", "This is the reference answer.")
# print(f"BARTScore: {score}")

In [ ]:
from datasets import load_dataset
import pandas as pd
from sklearn.model_selection import train_test_split

# Set seed for reproducibility
SEED = 42


dataset = load_dataset("pubmed_qa", "pqa_labeled")
df_pca = dataset['train'].select(range(1000))  # You can increase this later

# train_data = dataset["train"]
# test_data = dataset["test"]

# Show class balance before splitting
print("Original label distribution:\n", len(df_pca['final_decision']))

# Split into validation and test (e.g., 50/50 or 70/30)
df_val, df_test = train_test_split(
    df_pca,
    test_size=0.5,  # Or 0.3 for a 70/30 split
    random_state=42,
    stratify=df_pca['final_decision']  # Maintain label distribution
)

# Print sizes
print(f"Validation size: {len(df_val)}")
print(f"Test size: {len(df_test)}")

# Save splits if needed
df_val.to_csv("pubmedqa_pca_val.csv", index=False)
df_test.to_csv("pubmedqa_pca_test.csv", index=False)

def format_input(sample):
    return f"Question: {sample['question']}\nContext: {sample['context']}"


Original label distribution:
 1000


TypeError: '<' not supported between instances of 'int' and 'ellipsis'

In [ ]:
!pip install sacremoses


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 897.5/897.5 kB 28.2 MB/s eta 0:00:00


In [ ]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification, pipeline

cls_model_name = "microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract"
tokenizer_cls = AutoTokenizer.from_pretrained(cls_model_name)
model_cls = AutoModelForSequenceClassification.from_pretrained(cls_model_name, num_labels=3)
pipeline_cls = pipeline("text-classification", model=model_cls, tokenizer=tokenizer_cls)

sample_text = format_input(test_data[0])
print("Classification Prediction:", pipeline_cls(sample_text))

tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/385 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/225k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at microsoft/BiomedNLP-PubMedBERT-base-uncased-abstract and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Device set to use cuda:0


Classification Prediction: [{'label': 'LABEL_1', 'score': 0.4392710030078888}]


In [ ]:
print(len(test_data))

100


In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
import json
import time
from tqdm import tqdm  # progress bar
gen_model_name = "microsoft/BioGPT-Large"

# Load model and tokenizer
tokenizer_gen = AutoTokenizer.from_pretrained(gen_model_name)
model_gen = AutoModelForCausalLM.from_pretrained(gen_model_name)

# Move to GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_gen = model_gen.to(device)

# Load your test data (adjust path or variable as needed)
# Example: test_data = load_dataset("pubmed_qa", "pqa_artificial")["test"]
# Replace with your own test_data list of dicts if already loaded
assert 'test_data' in locals(), "Make sure test_data is already loaded before running this cell."

# 🔁 Answer generation function
def generate_answer(question, context):
    prompt = f"Question: {question}\nContext: {context}\nAnswer:"
    inputs = tokenizer_gen(prompt, return_tensors="pt", truncation=True, max_length=512)
    inputs = {k: v.to(device) for k, v in inputs.items()}
    outputs = model_gen.generate(**inputs, max_new_tokens=100)
    return tokenizer_gen.decode(outputs[0], skip_special_tokens=True)

# 📦 Output file and chunk save frequency
output_file = "bioqa_generated_answers.json"
save_every = 20  # save every N samples
results = []

# 🔄 Loop with periodic saving
start_time = time.time()

for i in tqdm(range(len(test_data)), desc="Generating answers"):
    q = test_data[i]["question"]
    c = test_data[i]["context"]

    try:
        a = generate_answer(q, c)
    except Exception as e:
        print(f"Error at index {i}: {e}")
        a = "Error: " + str(e)

    results.append({
        "index": i,
        "question": q,
        "context": c,
        "generated_answer": a
    })

    # Save every `save_every` examples
    if (i + 1) % save_every == 0 or (i + 1) == len(test_data):
        with open(output_file, "w") as f:
            json.dump(results, f, indent=2)
        print(f"✅ Saved {i + 1} samples to {output_file}")

end_time = time.time()
print(f"\n⏱️ Total time: {end_time - start_time:.2f} seconds")

tokenizer_config.json:   0%|          | 0.00/256 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.24M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/566k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/119 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/658 [00:00<?, ?B/s]

...

✅ Saved 60 samples to bioqa_generated_answers.json


Generating answers:  80%|████████  | 80/100 [04:45<00:53,  2.68s/it]

✅ Saved 80 samples to bioqa_generated_answers.json


Generating answers: 100%|██████████| 100/100 [06:06<00:00,  3.66s/it]

✅ Saved 100 samples to bioqa_generated_answers.json

⏱️ Total time: 366.03 seconds


In [ ]:
# Load generated predictions
with open("bioqa_generated_answers.json", "r") as f:
    predictions = json.load(f)

# Extract predicted answers and references
generated_answers = [item["generated_answer"] for item in predictions]
reference_answers = [test_data[item["index"]]["long_answer"] for item in predictions]  # assuming "long_answer" key exists


In [ ]:
print(predictions)

[{'index': 0, 'question': 'Does hippocampal atrophy on MRI predict cognitive decline?', 'context': {'contexts': ["To investigate whether the presence of hippocampal atrophy (HCA) on MRI in Alzheimer's disease (AD) leads to a more rapid decline in cognitive function. To investigate whether cognitively unimpaired controls and depressed subjects with HCA are at higher risk than those without HCA of developing dementia.", 'A prospective follow-up of subjects from a previously reported MRI study.', 'Melbourne, Australia.', 'Five controls with HCA and five age-matched controls without HCA, seven depressed subjects with HCA and seven without HCA, and 12 subjects with clinically diagnosed probable AD with HCA and 12 without HCA were studied. They were followed up at approximately 2 years with repeat cognitive testing, blind to initial diagnosis and MRI result.', 'HCA was rated by two radiologists blind to cognitive test score results. Cognitive assessment was by the Cambridge Cognitive Examina

In [ ]:
# !pip install bert-score --quiet
from bert_score import score
import json


# Compute BERTScore
P, R, F1 = score(generated_answers, reference_answers, lang="en", verbose=True)

# Display average score
print(f"\n🔍 BERTScore Results:")
print(f"Precision: {P.mean().item():.4f}")
print(f"Recall:    {R.mean().item():.4f}")
print(f"F1 Score:  {F1.mean().item():.4f}")


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

...

calculating scores...
computing bert embedding.


  0%|          | 0/4 [00:00<?, ?it/s]

computing greedy matching.


  0%|          | 0/2 [00:00<?, ?it/s]

done in 10.70 seconds, 9.35 sentences/sec

🔍 BERTScore Results:
Precision: 0.7642
Recall:    0.8747
F1 Score:  0.8156


In [ ]:
for i in range(5):  # View first 5 examples
    print(f"\nExample {i+1}")
    print("Generated:", generated_answers[i])
    print("Reference:", reference_answers[i])
    print(f"BERTScore F1: {F1[i].item():.4f}")



Example 1
Generated: Question: Does hippocampal atrophy on MRI predict cognitive decline? Context: {'contexts': ["To investigate whether the presence of hippocampal atrophy (HCA) on MRI in Alzheimer's disease (AD) leads to a more rapid decline in cognitive function. To investigate whether cognitively unimpaired controls and depressed subjects with HCA are at higher risk than those without HCA of developing dementia.", 'A prospective follow-up of subjects from a previously reported MRI study.', 'Melbourne, Australia.', 'Five controls with HCA and five age-matched controls without HCA, seven depressed subjects with HCA and seven without HCA, and 12 subjects with clinically diagnosed probable AD with HCA and 12 without HCA were studied. They were followed up at approximately 2 years with repeat cognitive testing, blind to initial diagnosis and MRI result.', 'HCA was rated by two radiologists blind to cognitive test score results. Cognitive assessment was by the Cambridge Cognitive Examin

In [ ]:
## Explainability with SHAP
import shap

explainer = shap.Explainer(pipeline_cls)
shap_values = explainer([sample_text])
shap.plots.text(shap_values[0])

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:21, 21.23s/it]               


In [ ]:
!pip install lime --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 275.7/275.7 kB 11.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done


In [ ]:
from lime.lime_text import LimeTextExplainer


In [ ]:
# You need to define a function that takes a list of texts and returns some scalar value (e.g., relevance or confidence of a keyword).

# Since BioGPT is generative, we’ll simulate it with a score based on keyword presence in the output.

In [ ]:
# Use BioGPT from before
def predict_fn(texts):
    scores = []
    for text in texts:
        prompt = f"Question: {text}\nContext: {test_data[0]['context']}\nAnswer:"
        inputs = tokenizer_gen(prompt, return_tensors="pt", truncation=True, max_length=512).to(device)
        outputs = model_gen.generate(**inputs, max_new_tokens=100)
        decoded = tokenizer_gen.decode(outputs[0], skip_special_tokens=True)
        # Example scoring: presence of the word "cancer"
        scores.append(1.0 if "cancer" in decoded.lower() else 0.0)
    return [[s, 1-s] for s in scores]  # LIME expects probability-like output


In [ ]:
explainer = LimeTextExplainer(class_names=["Mentions cancer", "Does not mention"])

# Run LIME on the question
# explanation = explainer.explain_instance(test_data[0]["question"], predict_fn, num_features=3)


explanation = explainer.explain_instance(
    test_data[0]["question"],
    predict_fn,
    num_features=3,
    num_samples=500  # Try 500 or even 200
)

# Show weights
explanation.show_in_notebook(text=True)

#Cant use LIME here , coz its not apt for Bio-GPT




KeyboardInterrupt: 

In [ ]:
#Training code for BioGPT LArge model

In [ ]:
!pip install evaluate scikit-learn


In [ ]:
# Install necessary libraries (if using Google Colab, uncomment the lines)
# !pip install transformers datasets torch

import torch
from datasets import load_dataset
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, Trainer, TrainingArguments
from transformers import pipeline




In [ ]:
!pip install -q -U bitsandbytes

In [ ]:

# Load only train split
dataset = load_dataset("pubmed_qa", "pqa_labeled")
train_valid_dataset = dataset["train"]

# Split manually: 90% train, 10% validation
split_dataset = train_valid_dataset.train_test_split(test_size=0.1, seed=42)
train_data = split_dataset["train"]
eval_data = split_dataset["test"]

In [ ]:


dataset = load_dataset("pubmed_qa", "pqa_labeled")
print(dataset)


DatasetDict({
    train: Dataset({
        features: ['pubid', 'question', 'context', 'long_answer', 'final_decision'],
        num_rows: 1000
    })
})


In [ ]:
# Load BioGPT tokenizer and model

from transformers import AutoModelForCausalLM,BitsAndBytesConfig
# base_model_id = "meta-llama/Llama-2-7b-hf"
model_name = "microsoft/BioGPT-Large"
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

# tokenizer = AutoTokenizer.from_pretrained(model_name)
# model = AutoModelForCausalLM.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name, quantization_config=bnb_config, device_map="auto")





In [ ]:
tokenizer = AutoTokenizer.from_pretrained(
    model_name,
    padding_side="left",
    add_eos_token=True,
    add_bos_token=True,
)
tokenizer.pad_token = tokenizer.eos_token

# def generate_and_tokenize_prompt(prompt):
#     return tokenizer(formatting_func(prompt))

In [ ]:
# Preprocess: combine question, context, and answer into a single string
def preprocess(example):
    input_text = f"Question: {example['question']} Context: {example['context']} Answer:"
    target_text = f" {example['long_answer']}"
    full_text = input_text + target_text

    tokenized = tokenizer(full_text, truncation=True, padding="max_length", max_length=512)
    tokenized["labels"] = tokenized["input_ids"].copy()
    return tokenized


In [ ]:
# Apply preprocessing
train_dataset = train_data.map(preprocess, remove_columns=train_data.column_names)
eval_dataset = eval_data.map(preprocess, remove_columns=eval_data.column_names)

# Set format for PyTorch
train_dataset.set_format("torch")
eval_dataset.set_format("torch")

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

Map:   0%|          | 0/100 [00:00<?, ? examples/s]

In [ ]:
from transformers import DataCollatorForLanguageModeling


# Data collator for causal language modeling
data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)

# Training arguments

In [ ]:
# Now, to start our fine-tuning, we have to apply some preprocessing to the model to prepare it for training.
#  For that use the prepare_model_for_kbit_training method from PEFT.

from peft import prepare_model_for_kbit_training

model.gradient_checkpointing_enable()
model = prepare_model_for_kbit_training(model)

In [ ]:
def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

In [ ]:
print(model)

BioGptForCausalLM(
  (biogpt): BioGptModel(
    (embed_tokens): BioGptScaledWordEmbedding(57717, 1600, padding_idx=1)
    (embed_positions): BioGptLearnedPositionalEmbedding(2050, 1600)
    (layers): ModuleList(
      (0-47): 48 x BioGptDecoderLayer(
        (self_attn): BioGptSdpaAttention(
          (k_proj): Linear4bit(in_features=1600, out_features=1600, bias=True)
          (v_proj): Linear4bit(in_features=1600, out_features=1600, bias=True)
          (q_proj): Linear4bit(in_features=1600, out_features=1600, bias=True)
          (out_proj): Linear4bit(in_features=1600, out_features=1600, bias=True)
        )
        (activation_fn): GELUActivation()
        (self_attn_layer_norm): LayerNorm((1600,), eps=1e-05, elementwise_affine=True)
        (fc1): Linear4bit(in_features=1600, out_features=6400, bias=True)
        (fc2): Linear4bit(in_features=6400, out_features=1600, bias=True)
        (final_layer_norm): LayerNorm((1600,), eps=1e-05, elementwise_affine=True)
      )
    )
    (

In [ ]:
from peft import LoraConfig, get_peft_model

config = LoraConfig(
    r=32,
    lora_alpha=64,
    target_modules=[
        "q_proj",
        "k_proj",
        "v_proj",
        "o_proj",
        "gate_proj",
        "up_proj",
        "down_proj",
        "lm_head",
    ],
    bias="none",
    lora_dropout=0.05,  # Conventional
    task_type="CAUSAL_LM",
)

model = get_peft_model(model, config)
print_trainable_parameters(model)

# Apply the accelerator. You can comment this out to remove the accelerator.
# model = accelerator.prepare_model(model)

/usr/local/lib/python3.11/dist-packages/peft/mapping_func.py:73: UserWarning: You are trying to modify a model with PEFT for a second time. If you want to reload the model with a different config, make sure to call `.unload()` before.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/peft/tuners/tuners_utils.py:167: UserWarning: Already found a `peft_config` attribute in the model. This will lead to having multiple adapters in the model. Make sure to know what you are doing!
  warnings.warn(


trainable params: 14745600 || all params: 848654400 || trainable%: 1.7375270781604384


In [ ]:
print(model)

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): PeftModelForCausalLM(
      (base_model): LoraModel(
        (model): BioGptForCausalLM(
          (biogpt): BioGptModel(
            (embed_tokens): BioGptScaledWordEmbedding(57717, 1600, padding_idx=1)
            (embed_positions): BioGptLearnedPositionalEmbedding(2050, 1600)
            (layers): ModuleList(
              (0-47): 48 x BioGptDecoderLayer(
                (self_attn): BioGptSdpaAttention(
                  (k_proj): lora.Linear4bit(
                    (base_layer): Linear4bit(in_features=1600, out_features=1600, bias=True)
                    (lora_dropout): ModuleDict(
                      (default): Dropout(p=0.05, inplace=False)
                    )
                    (lora_A): ModuleDict(
                      (default): Linear(in_features=1600, out_features=32, bias=False)
                    )
                    (lora_B): ModuleDict(
                      (default): Linear(in_features=32, out_fe

In [ ]:
!pip install -q wandb -U

import wandb, os
wandb.login()

wandb_project = "biomodel_qa"
if len(wandb_project) > 0:
    os.environ["WANDB_PROJECT"] = wandb_project

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: priyanka_mn to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [ ]:
import transformers
from datetime import datetime

project = "biomodel_qa"
base_model_name = "biogpt-large"
run_name = base_model_name + "-" + project
output_dir = "./" + run_name

tokenizer.pad_token = tokenizer.eos_token

trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    args=transformers.TrainingArguments(
        output_dir=output_dir,
        warmup_steps=1,
        per_device_train_batch_size=2,
        gradient_accumulation_steps=1,
        gradient_checkpointing=True,
        max_steps=500,
        learning_rate=2.5e-5, # Want a small lr for finetuning
        bf16=True,
        optim="paged_adamw_8bit",
        logging_dir="./logs",        # Directory for storing logs
        save_strategy="steps",       # Save the model checkpoint every logging step
        save_steps=50,                # Save checkpoints every 50 steps
        eval_strategy="steps", # Evaluate the model every logging step
        eval_steps=50,               # Evaluate and save checkpoints every 50 steps
        do_eval=True,                # Perform evaluation at the end of training
        report_to="wandb",           # Comment this out if you don't want to use weights & baises
        run_name=f"{run_name}-{datetime.now().strftime('%Y-%m-%d-%H-%M')}"          # Name of the W&B run (optional)
    ),
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)

model.config.use_cache = False  # silence the warnings. Please re-enable for inference!
trainer.train()

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.11/dist-packages/peft/utils/save_and_load.py:220: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

TrainOutput(global_step=500, training_loss=1.91178955078125, metrics={'train_runtime': 3460.901, 'train_samples_per_second': 0.289, 'train_steps_per_second': 0.144, 'total_flos': 4578223718400000.0, 'train_loss': 1.91178955078125, 'epoch': 1.1111111111111112})

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

base_model_id = "microsoft/BioGPT-Large"

base_model = AutoModelForCausalLM.from_pretrained(
    base_model_id,  # BioGPT-Large, same as before
    quantization_config=bnb_config,  # Same quantization config as before
    device_map="auto",
    trust_remote_code=True,
)

tokenizer = AutoTokenizer.from_pretrained(base_model_id, add_bos_token=True, trust_remote_code=True)

In [ ]:
from peft import PeftModel

ft_model = PeftModel.from_pretrained(base_model, "/content/biogpt-large-biomodel_qa/checkpoint-500")

/usr/local/lib/python3.11/dist-packages/peft/peft_model.py:569: UserWarning: Found missing adapter keys while loading the checkpoint: ['base_model.model.biogpt.layers.0.self_attn.k_proj.lora_A.default.weight', 'base_model.model.biogpt.layers.0.self_attn.k_proj.lora_B.default.weight', 'base_model.model.biogpt.layers.0.self_attn.v_proj.lora_A.default.weight', 'base_model.model.biogpt.layers.0.self_attn.v_proj.lora_B.default.weight', 'base_model.model.biogpt.layers.0.self_attn.q_proj.lora_A.default.weight', 'base_model.model.biogpt.layers.0.self_attn.q_proj.lora_B.default.weight', 'base_model.model.biogpt.layers.1.self_attn.k_proj.lora_A.default.weight', 'base_model.model.biogpt.layers.1.self_attn.k_proj.lora_B.default.weight', 'base_model.model.biogpt.layers.1.self_attn.v_proj.lora_A.default.weight', 'base_model.model.biogpt.layers.1.self_attn.v_proj.lora_B.default.weight', 'base_model.model.biogpt.layers.1.self_attn.q_proj.lora_A.default.weight', 'base_model.model.biogpt.layers.1.self_a

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
import json
import time
from tqdm import tqdm  # progress bar
# gen_model_name = ft_model

# # Load model and tokenizer
# # tokenizer_gen = AutoTokenizer.from_pretrained(gen_model_name)
# model_gen = AutoModelForCausalLM.from_pretrained(gen_model_name)

# Move to GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_gen = ft_model.to(device)

# Load your test data (adjust path or variable as needed)
# Example: test_data = load_dataset("pubmed_qa", "pqa_artificial")["test"]
# Replace with your own test_data list of dicts if already loaded
assert 'test_data' in locals(), "Make sure test_data is already loaded before running this cell."

# 🔁 Answer generation function
def generate_answer(question, context):
    prompt = f"Question: {question}\nContext: {context}\nAnswer:"
    inputs = tokenizer(prompt, return_tensors="pt", truncation=True, max_length=512)
    inputs = {k: v.to(device) for k, v in inputs.items()}
    outputs = model_gen.generate(**inputs, max_new_tokens=100)
    return tokenizer.decode(outputs[0], skip_special_tokens=True)

# 📦 Output file and chunk save frequency
output_file = "ft_bioqa_generated_answers.json"
save_every = 20  # save every N samples
results = []

# 🔄 Loop with periodic saving
start_time = time.time()

for i in tqdm(range(len(test_data)), desc="Generating answers"):
    q = test_data[i]["question"]
    c = test_data[i]["context"]

    try:
        a = generate_answer(q, c)
    except Exception as e:
        print(f"Error at index {i}: {e}")
        a = "Error: " + str(e)

    results.append({
        "index": i,
        "question": q,
        "context": c,
        "generated_answer": a
    })

    # Save every `save_every` examples
    if (i + 1) % save_every == 0 or (i + 1) == len(test_data):
        with open(output_file, "w") as f:
            json.dump(results, f, indent=2)
        print(f"✅ Saved {i + 1} samples to {output_file}")

end_time = time.time()
print(f"\n⏱️ Total time: {end_time - start_time:.2f} seconds")

Generating answers:  20%|██        | 20/100 [03:01<10:24,  7.80s/it]

✅ Saved 20 samples to ft_bioqa_generated_answers.json


Generating answers:  40%|████      | 40/100 [06:26<07:56,  7.95s/it]

✅ Saved 40 samples to ft_bioqa_generated_answers.json


Generating answers:  60%|██████    | 60/100 [09:37<06:34,  9.86s/it]

✅ Saved 60 samples to ft_bioqa_generated_answers.json


Generating answers:  80%|████████  | 80/100 [13:01<03:51, 11.60s/it]

✅ Saved 80 samples to ft_bioqa_generated_answers.json


Generating answers: 100%|██████████| 100/100 [15:59<00:00,  9.60s/it]

✅ Saved 100 samples to ft_bioqa_generated_answers.json

⏱️ Total time: 959.92 seconds


In [ ]:
# Load generated predictions
with open("ft_bioqa_generated_answers.json", "r") as f:
    predictions = json.load(f)

# Extract predicted answers and references
generated_answers = [item["generated_answer"] for item in predictions]
reference_answers = [test_data[item["index"]]["long_answer"] for item in predictions]  # assuming "long_answer" key exists


In [ ]:
# !pip install bert-score --quiet
from bert_score import score
import json


# Compute BERTScore
P, R, F1 = score(generated_answers, reference_answers, lang="en", verbose=True)

# Display average score
print(f"\n🔍 BERTScore Results:")
print(f"Precision: {P.mean().item():.4f}")
print(f"Recall:    {R.mean().item():.4f}")
print(f"F1 Score:  {F1.mean().item():.4f}")


Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


calculating scores...
computing bert embedding.


  0%|          | 0/4 [00:00<?, ?it/s]

computing greedy matching.


  0%|          | 0/2 [00:00<?, ?it/s]

done in 10.89 seconds, 9.19 sentences/sec

🔍 BERTScore Results:
Precision: 0.7645
Recall:    0.8758
F1 Score:  0.8163


In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)


In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
from lime.lime_text import LimeTextExplainer
from sklearn.metrics.pairwise import cosine_similarity
import torch
import numpy as np

# Load BioGPT model and tokenizer
model_name = "microsoft/biogpt"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name).eval().to("cuda" if torch.cuda.is_available() else "cpu")

# Reference answer (the ideal answer)
reference_answer = "Yes, aspirin helps reduce the risk of heart attacks."

config.json:   0%|          | 0.00/595 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/927k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/696k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.56G [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.56G [00:00<?, ?B/s]

In [ ]:
import torch
torch.cuda.empty_cache()
